In [1]:
import time
import requests
from bs4 import BeautifulSoup
from datetime import date
import json

In [2]:
class PageScrapper:

    def __init__(self, url):

        self.url = url
        self.last_page = self.get_last_page_number()
        
        self.data_dict = {}
        self.data_index=0
        
        print(f"Total number of pages: {self.last_page}")

    def get_last_page_number(self):
        page = self.read_page_content(self.url)
        container = page.find('ul', {'class': 'pager'})
        last_page_element = container.findAll("a", {'class': ''})[-2]
        return int(last_page_element.getText())

    def find_advertisements(self):
      
        for page_number in range(self.last_page + 1):

            print(f"Page {page_number+1}/{self.last_page} processing...")

            page = self.read_page_content(self.url + f'&page={page_number+1}')
            container = page.findAll("header", {"class": "offer-item-header"})
            
                    
            for advertisement_index in range(len(container)):
                advertisement = container[advertisement_index].find('a')
                data=(self.parse_advertisement(advertisement.get('href')))
                #print(data)
                self.data_dict[self.data_index] = data
                self.data_index+=1
#                 self.save_data_json(data)
                time.sleep(1)
                
        

    def parse_advertisement(self, url):

        print(url)
        data = {}

        page = self.read_page_content(url)
        
        
        try: 
            data['tytul'] = page.find('h1', {'class': 'css-1ld8fwi'}).get_text().strip()
        except:
            pass
    
        try: 
            data['adres'] = page.find('a', {'class': 'css-12hd9gg'}).get_text().strip()
        except:
            pass
        
        try: 
            data['imie']=next(page.find('div', {'class': 'css-1rg48tw'}).stripped_strings)
        except:
            pass
        
        try:
            data['biuro_nieruchomosci']=page.find('li',{'class':'css-1uzc6ks'}).get_text()
        except:
            pass
        
        try:
            container=page.find('section',{'class':'section-description'}).findAll('p')

            opis=''

            for i in range (len(container)):
                opis=opis+container[i].get_text()
                data['tresc']=opis
        except:
               pass
           
        try:
            data['cena_za_metr'] = (page.find('div', {'class': 'css-zdpt2t'})
                             .get_text().replace('zł', '').replace('/m²', '').replace(' ', '').replace(',', '.'))
        except:
            pass
        
        try:
            data['cena'] = (page.find('div', {'class': 'css-1vr19r7'})
                             .get_text().replace('zł', '').replace(' ', '').replace(',', '.'))
        except:
            pass
        try:
            data['oferta'] = (page.find('div', {'class': 'css-1gjwmw9'})
                             .get_text())
        except:
            pass
             
        try:
            data['liczba_zdjec'] = (page.find('span', {'class': 'slick-npages'})
                             .get_text().replace('1/', ''))
        except:
            pass
        
        try:
            data_dodania_aktualizacji = (page.find('div', {'class': 'css-lh1bxu'})
                                 .get_text()).split('Data')


            data['data']=data_dodania_aktualizacji[1].split(':')[1]
            data['data_aktualizacji']=data_dodania_aktualizacji[2].split(':')[1]
        except:
            pass
        
        try:
            numer_oferty = (page.find('div', {'class': 'css-kos6vh'})
                                 .get_text()).split('Nr')

            data['numer_otodom']=numer_oferty[1].split(':')[1]
            data['numer_biura_nieruchomosci']=numer_oferty[2].split(':')[1]
        except :
            pass
        
        
        
        #INFORAMCJE DODATKOWE
        try:
            container = page.find('div',{'class':'css-1bpegon'}).findAll('li')
            for li in container:
                key=li.get_text()
                data[key]=True
        except:
            pass
        
        try:
            container=page.find('div',{'class':'css-1ci0qpi'}).findAll('li')

            for li in container:
                slownik=li.get_text().split(':')
                key=slownik[0]
                value=slownik[1].replace(' ', '')
                data[key]=value
        except:
            pass 
            
        try:
            data['json'] = page.find('script', {'id': 'server-app-state'})
        except:
            pass
            

        return data

    def read_page_content(self, url):
        page = requests.get(url)
        return BeautifulSoup(page.content, "html.parser")

    def create_json(self):
        with open('data_otodom.json', 'w') as fp:
            json.dump(self.data_dict, fp)


URL = 'https://www.otodom.pl/sprzedaz/mieszkanie/?locations%5B0%5D%5Bregion_id%5D=11&locations%5B0%5D%5Bcity_id%5D=206&locations%5B1%5D%5Bregion_id%5D=11&locations%5B1%5D%5Bcity_id%5D=208&locations%5B2%5D%5Bregion_id%5D=11&locations%5B2%5D%5Bcity_id%5D=40&search%5Border%5D=created_at_first%3Adesc'
scraper = PageScrapper(URL)
scraper.find_advertisements()
scraper.create_json()

Total number of pages: 299
Page 1/299 processing...
https://www.otodom.pl/oferta/2-pokoje-marzenie-gdansk-zabianka-ID45xdP.html#88204099a8
{'tytul': '2 pokoje - marzenie Gdańsk Żabianka', 'adres': 'Gdańsk, Żabianka, ul. Gdyńska', 'imie': 'Jakub', 'tresc': 'Mieszkanie-marzenie, które mimo niewielkiego metrażu zyskało podczas generalnego remontu wielką funkcjonalność - osobną sypialnię z podwójnym łóżkiem, szafą we wnęce i 22-metrowy pokój z aneksem kuchennym.Nowoczesna aranżacja z betonem architektonicznym zaprasza do salonu, gdzie nawet podczas kwarantanny nie zabraknie nam przestrzeni - okna na całej długości sprawiają, że mieszkanie jest pełne słońca, a francuski balkon umożliwia zrobienie osobistego zejścia do ogródka - nie lada gratka w samym centrum miasta. 2-osobowa kabina prysznicowa na całej szerokości łazienki zapewnia wyjątkowy komfort kąpieli.Doskonała lokalizacja w sercu Gdańska Żabianki na ul. Gdyńskiej pozwoli oszczędzać czas każdego dnia - spacer 8 min. do stacji SKM i p

https://www.otodom.pl/oferta/gotowe-7km-do-centrum-2km-do-plazy-ID45GaC.html#88204099a8
{'tytul': 'Gotowe , 7km do Centrum, 2km do plaży', 'adres': 'Gdynia, Oksywie, inż. J. Śmidowicza', 'imie': 'NOWE MIESZKANIA', 'biuro_nieruchomosci': 'BIURO SPRZEDAŻY', 'tresc': 'Bezpośrednio z biura sprzedaży dewelopera ! termin realizacji maj 2020r!Oferta promocyjna ważna do końca kwietnia!W ofercie również inne rozkłady mieszkań !WYSOKIE RABATY TYLKO W KWIETNIU !!Gdynia , ul.ŚmidowiczaUdogodnienia: bliskość do plaży (ok. 2 km), sąsiedztwo lasu, bogata infrastruktura, pełne zaplecze handlowo-usługowe, place zabaw, mieszkania z pakietem antysmogowym i opcją smart home/energooszczędne. Przynależności: balkon, ogródek, taras, komórka lokatorska Bezpieczeństwo: domofon Wielkość projektu: w całej inwestycji - 579 mieszkań zaprojektowanych w 6 budynkach. 1 budynek oddany do użytku, 3 budynki aktualnie w ofercie. Garaże: podziemna hala garażowa, dostępne również miejsca naziemne Komunikacja: autobus - 150

https://www.otodom.pl/oferta/gdansk-lostowice-3-pokoje-do-wejscia-ID45G9a.html#88204099a8
{'tytul': 'Gdańsk Łostowice 3 pokoje do wejścia', 'adres': 'Gdańsk, Ujeścisko-Łostowice, ul. Olimpijska', 'imie': 'Maciej Polański', 'biuro_nieruchomosci': 'Biuro Nieruchomości HB Jakuba Zarzeckiego', 'tresc': 'Przestronne trzypokojowe mieszkanie na trzecim piętrze w bloku 3-piętrowym w Gdańsku - Łostowice.Mieszkanie trójstronne z oknami wychodzącymi na północ, wschód, zachód, z widokiem na inne budynki.W skład mieszkania wchodzą: salon z aneksem kuchennym, dwie sypialnie, łazienka, WC oraz przedpokój.Wykończenie: Podłogi - terakota, panele podłogowe; Ściany - gładź gipsowa, glazura; Parapety - konglomerat; Okna - PCV.Do mieszkania przynależy piwnica oraz balkon.Do dyspozycji mieszkańców jest: plac zabaw oraz parking ogólnodostępny zlokalizowany na terenie wspólnoty za szlabanem. W najbliższej okolicy znajduje się przystanek autobusowy, sklep- Biedronka, Żabka oraz nieopodal punkty usługowe.Czynsz

https://www.otodom.pl/oferta/oddzielna-kuchni-2-pokoje-idealnie-skomunikowane-ID45G89.html#88204099a8
{'tytul': 'Oddzielna kuchni, 2 pokoje idealnie skomunikowane!', 'adres': 'Gdańsk, Jasień', 'imie': 'Iga Turska', 'biuro_nieruchomosci': 'BALTIC Hus', 'tresc': 'MIESZKANIE O POWIERZCHNI 54 M2, ODDZIELNA KUCHNIA, SALON ORAZ SYPIALNIA, DUŻY BALKONJasień to dzielnica Gdańska, która podlega w ostatnich latach intensywnej rozbudowie - zarówno w zakresie zabudowy mieszkaniowej, jak i handlowo-usługowej. To tutaj powstał Fashion House Outlet Center, tu otwierane są kolejne centra handlowe i sklepy wielkopowierzchniowe. Wokół samego Osiedla roztaczają się naturalne tereny. Budynki osiedla powstają między dwoma otoczonymi zielenią potokami. Potoki przechodzą w mały zbiornik wodny, którego linia brzegowa od północy styka się z osiedlem. Mieszkanie jest bardzo zadbane, zamieszkane jedynie weekendowo.Wnętrze jest bardzo przestrzenne, jasne. Istnieje możliwość przeniesienia aneksu kuchennego do salo

https://www.otodom.pl/oferta/mieszkanie-sopot-centrum-ID45G3p.html#88204099a8
{'tytul': 'Mieszkanie - Sopot Centrum', 'adres': 'Sopot, Centrum', 'imie': 'Jolanta Płonka', 'biuro_nieruchomosci': 'Nieruchomości Ewa Krzesińska', 'tresc': 'Komfortowe mieszkanie położone na pierwszym pietrze w stylowej kamienicy.Doskonała lokalizacja, Centrum miasta, blisko mola, przystanków autobusowych i SKM.Mieszkanie składa się z sypialni, salonu z którego jest wejście do jasnej kuchni, łazienki razem z WC oraz przedpokoju. Ogrzewanie gazowe.W cenie mieszkania pozostaje całe umeblowanie wraz ze sprzętem AGD.Budynek usytuowany jest w górnej, bardziej zacisznej części ul. Monte Cassino.', 'cena_za_metr': '12307', 'cena': '589000', 'oferta': 'Oferta biura nieruchomości', 'liczba_zdjec': ' 10', 'data_dodania': ' około 8 godzin temu', 'data_aktualizacji': ' około 8 godzin temu', 'numer_otodom': ' 60458643', 'numer_biura_nieruchomosci': ' KE05695', 'internet': True, 'telefon': True, 'domofon / wideofon': True

...

https://www.otodom.pl/oferta/mieszkanie-z-anteresola-do-wlasnej-aranzacji-ID45fwr.html#0a2fe70b21
{'tytul': 'Mieszkanie z anteresolą do własnej aranżacji', 'adres': 'Gdynia, Wielki Kack', 'imie': 'Daria Dolecińska', 'biuro_nieruchomosci': 'Navigat Nieruchomości', 'tresc': 'Mieszkania na sprzedaż zlokalizowane są w dzielnicy Wielki Kack w Gdyni, nieopodal parku krajobrazowego i centrum miasta. Dzięki temu, osoby decydujące się na prezentowaną inwestycję zyskują przestronne lokale położone w zielonej, urokliwej okolicy, zapewniającej łatwe połączenie z kluczowymi miejscami w mieście. To idealne rozwiązanie m.in. dla rodzin z dziećmi, biegaczy, rowerzystów oraz miłośników aktywności fizycznej, a także osób ceniących mnogość tras spacerowych i malowniczą, spokojną okolicę.Inwestycja składa się z wielorodzinnych osiedli z niską zabudową, zapewniające sielski klimat.Ustronny charakter osiedla uzyskano dzięki niskiej, trzykondygnacyjnej zabudowie.Dwupoziomowe mieszkanie o powierzchni 95,55 m2

https://www.otodom.pl/oferta/mieszkanie-z-przestronnym-salonem-ID45fwj.html#0a2fe70b21
{'tytul': 'Mieszkanie z przestronnym salonem', 'adres': 'Kazimierza Wielkiego, Gdańsk, pomorskie', 'imie': 'Marlena Tomala', 'biuro_nieruchomosci': 'MyPlace', 'tresc': 'Niezależność, bezpieczeństwo, przestrzeń oraz cisza i spokój..., to wszystko zapewni Państwu nowo powstające Osiedle Maciejka przy ulicy Borkowskiej w Gdańsku. Po zgiełku miejskiego życia przed mieszkańcami Osiedla Maciejka pojawia się możliwość wyciszenia i wypoczynku w przyjaznym otoczeniu malowniczej przyrody. Kameralny charakter zapewni Państwu niewielka liczba budynków. Nowoczesna architektura, staranność detali oraz otaczająca zieleń tworzą niepowtarzalny klimat tego miejsca.Przy projektowaniu osiedla szczególną uwagę zwróciliśmy na bezpieczeństwo-teren będzie w całości ogrodzony z zamkniętym wjazdem. Dla wygody rodziców i ku uciesze dzieci zaprojektowaliśmy także plac zabaw. W trzech budynkach zaprojektowano cichobieżne windy, 

https://www.otodom.pl/oferta/2-pokojowe-mieszkanie-witomino-witawa-ID45fqh.html#0a2fe70b21
{'tytul': '2 pokojowe mieszkanie Witomino - Witawa!', 'adres': 'Gdynia, Witomino, Niska', 'imie': 'Aleksandra Węgrzyn', 'biuro_nieruchomosci': 'Artflat Nieruchomości', 'tresc': 'Przedmiotem sprzedaży jest 2 - pokojowe mieszkanie usytuowane w budynku CR Witawa z 2002 roku w Gdyni Witomino, przy ul. Niskiej. Budynek z całodobową portiernią i monitoringiem, wyposażony w zewnętrzne patio\xa0 z ogrodem i placem zabaw dla dzieci. Wewnątrz budynku znajduje się centrum handlowo - usługowe (sklepy, poczta, fryzjer, kosmetyczka, pralnia, siłownia), a na poziomie -1 trzypoziomowa hala garażowa z miejscami postojowymi dla mieszkańców i gości.  Mieszkanie posiada powierzchnię 55 m2 i składa się z: przestronnego pokoju dziennego z aneksem kuchennym, z którego jest wyjście na słoneczny BALKON; ustawnej sypialni, przedpokoju z szafą w zabudowie oraz łazienki z kabiną prysznicową. Na tym samym piętrze co mieszkan

https://www.otodom.pl/oferta/gdansk-3-pokojowe-z-widokiem-na-las-ID45fkq.html#0a2fe70b21
{'tytul': 'Gdańsk 3 pokojowe z widokiem na las', 'adres': 'Gdańsk, Matarnia, mjr. Mieczysława Słabego', 'imie': 'Judyta Cadko', 'biuro_nieruchomosci': 'Deal Estate', 'tresc': 'NA SPRZEDAŻ 3 POKOJOWE MIESZKANIE Z PIEKNYM WIDOKIEM NA LASATUTY NIERUCHOMOŚCI:- trzy niezależne pokoje- widok z okien na tereny zielone- niska, kameralna zabudowa- sąsiedztwo Trójmiejskiego Parku Krajobrazowego,- pełne zaplecze handlowo-usługowe w okolicy,- szkoła w odległości 20m,- 100m do przystanku autobusowego linii 110, 122, 126, 157, 210, N3- 2 minuty do obwodnicy, 10 minut do Lotniska im. Lecha Wałęsy- 10 minut do Wrzeszcza/15 minut do Gdańska Głównego- staranne i wysokiej jakości wykończenieCHARAKTERYSTYKANa sprzedaż trzypokojowe mieszkanie o powierzchni 57,1m2 znajdujące się na czwartym piętrzę w pięciokondygnacyjnym nowoczesny bloku dewelopera Krj z 2017 znajdującym się na osiedlu Cztery Kąty w Gdańsku na Złotej Ka

AttributeError: 'NoneType' object has no attribute 'get_text'